In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
plt.style.use('paper_1column.mplstyle')
import datetime
import time
import os
import sys
from pathlib import Path
import folium
import branca.colormap as cm
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from joblib import dump
from joblib import load

In [2]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Activation, Dense
from tensorflow.keras.optimizers import SGD
from tensorflow.keras.metrics import categorical_crossentropy
from tensorflow.keras.models import Model

Train = False

2023-03-12 13:57:42.904716: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [3]:
physical_devices = tf.config.experimental.list_physical_devices('GPU')
print("Num GPUs Available: ", len(physical_devices))
# tf.config.experimental.set_memory_growth(physical_devices[0], True)

Num GPUs Available:  0


In [4]:
# model.compile(optimizer=Adam(learning_rate=0.0001), loss=tf.keras.losses.MeanSquaredError(), metrics=['accuracy'])

In [5]:
def standardize(V):
    if np.std(V) == 0:
        return np.zeros((len(V),1))
    else: 
        return((V-np.mean(V))/np.var(V))

In [6]:
def convert24(tim):
    # Parse the time string into a datetime object
    t = datetime.datetime.strptime(tim, '%I:%M:%S %p')
    # Format the datetime object into a 24-hour time string
    return t.strftime('%H:%M:%S')

In [7]:
def gen_darkhours(X1, y1):
    X2 = np.zeros((1,3))
    y2 = np.zeros((1,1))
    X1_ = np.copy(X1)
    y1_ = np.zeros((len(X1),1))
    y1_[:] = np.random.normal(8.83, 0.2, size=(len(X1),1))
    for i in [22, 23, 0, 1, 2, 3, 4, 5, 6]:
        X1_[:,2] = i*3600
        X2 = np.concatenate((X2,X1_))
        y2 = np.concatenate((y2,y1_))
    y1_[:] = np.random.normal(7.5, 0.2, size=(len(X1),1))
    for i in [21, 7]:
        X1_[:,2] = i*3600
        X2 = np.concatenate((X2,X1_))
        y2 = np.concatenate((y2,y1_))
    X2 = X2[1:,:]
    y2 = y2[1:,:]
    return X2, y2

In [8]:
def data_process(filename):
    data_pd = pd.read_csv(filename, sep=',',header=0, usecols = range(6))
    data_pd.columns = ['StartTime','Lat','Long','Velocity','Time','Time Offset']
    data_pd = data_pd.dropna()
    num_rows = len(data_pd["Lat"])
    data_pd = data_pd.reset_index(drop=True)
    data_pd = data_pd.drop(range(num_rows-10, num_rows))
    data_pd = data_pd.drop(range(10))
    data_pd = data_pd.reset_index(drop=True)
    drop_arr = []
    num_rows = len(data_pd["Lat"])
    for i in range(num_rows):
        if "Err" in data_pd.iloc[i]['StartTime']:
            drop_arr.append(i)
    data_pd = data_pd.drop(drop_arr)
    num_rows = len(data_pd["Lat"])
    data_pd = data_pd.reset_index(drop=True)
    drop_arr2 = []
    for i in range(num_rows):
        if "NUM" in data_pd.iloc[i]['StartTime']:
            drop_arr2.append(i)
    data_pd = data_pd.drop(drop_arr2)
    num_rows = len(data_pd["Lat"])
    data_pd = data_pd.reset_index(drop=True)
#     for i in range(num_rows-1):
#         vel_vec[i] = np.sqrt((data_pd.iloc[i+1]["Lat"] - data_pd.iloc[i]["Lat"])**2\
#                              + (data_pd.iloc[i+1]["Long"] - data_pd.iloc[i]["Long"])**2)
#                              #+ (data_pd.iloc[i+1]["Altitude"] - data_pd.iloc[i]["Altitude"])**2)\
#         #/(data_pd.iloc[i+1]["TimeNano"]/10**9 - data_pd.iloc[i]["TimeNano"]/10**9)
    lat_vec = np.array(data_pd["Lat"])
    long_vec = np.array(data_pd["Long"])
#     conj_vec = 1/np.exp(vel_vec)
    time_vec = np.array(data_pd["StartTime"])
    vel_vec = np.array(data_pd["Velocity"])
    time_sec_vec = []
    for i in range(num_rows):
        if 'AM' not in time_vec[i] and 'PM' not in time_vec[i]:
            x = time.strptime(time_vec[i],'%H:%M:%S')
            time_sec_vec.append(datetime.timedelta(hours=x.tm_hour,minutes=x.tm_min,seconds=x.tm_sec).total_seconds())
        else:
#             print(time_vec[i])
#             print(convert24(time_vec[i]))
            x = time.strptime(convert24(time_vec[i]),'%H:%M:%S')
            time_sec_vec.append(datetime.timedelta(hours=x.tm_hour,minutes=x.tm_min,seconds=x.tm_sec).total_seconds())
            
    #X = np.transpose(np.array([lat_vec, long_vec, time_sec_vec]))
    X = np.transpose(np.array([lat_vec.astype(float), long_vec.astype(float), time_sec_vec]))
    y = np.zeros((num_rows, 1))
    for i in range(num_rows):
        y[i] = vel_vec[i]
    i = 0
    while i < len(X):
        if float(X[i,0]) < 37.42+0.0026:
            X = np.delete(X, (i), axis = 0)
            y = np.delete(y, (i), axis = 0)
            i = i - 1
        if float(X[i,0]) < 37.42+0.0043 and float(X[i,1]) > -122.1-0.0605:
            X = np.delete(X, (i), axis = 0)
            y = np.delete(y, (i), axis = 0)
            i = i - 1
        i = i + 1
    return X, y

In [9]:
Dark = True
Time_dep = True

Directory = '/Users/shirleychen/Documents/Winter2023/AA272/Project/GoodCSVs/'
pathlist = Path(Directory).rglob('*.csv')
X_real = np.zeros((1,3))
y_real = np.zeros((1,1))
X_dark = np.zeros((1,3))
y_dark = np.zeros((1,1))
for path in pathlist:
    X1, y1 = data_process(path)
    X2, y2 = gen_darkhours(X1, y1)
    X_dark = np.concatenate((X_dark,X2))
    y_dark = np.concatenate((y_dark,y2))
    X_real = np.concatenate((X_real,X1))
    y_real = np.concatenate((y_real,y1))
X_real = X_real[1:,:]
y_real = y_real[1:,:]
X_dark = X_dark[1:,:]
y_dark = y_dark[1:,:]
if Dark == True:
    X = np.concatenate((X_real,X_dark))
    y = np.concatenate((y_real,y_dark))
else:
    X = np.copy(X_real)
    y = np.copy(y_real)
print("Real data size:", np.size(y_real))
print("Dark data size:", np.size(y_dark))
print("Total data size:", np.size(y))

if Time_dep == False:
    X = X[:,0:2]
    X_real = X_real[:,0:2]
    X_dark = X_dark[:,0:2]

Real data size: 6875
Dark data size: 75625
Total data size: 82500


In [10]:
# standardize dataset
y_real_scaled = StandardScaler().fit_transform(y.reshape(len(y),1))[:,0]
scaler = StandardScaler()
scaler.fit(X)
X = scaler.transform(X)
dump(scaler, 'scaler.joblib')
#X = StandardScaler().fit_transform(X)
scalery = StandardScaler()
scalery.fit(y.reshape(len(y),1))
y = scalery.transform(y.reshape(len(y),1))[:,0]
dump(scalery, 'scalery.joblib')

['scalery.joblib']

In [11]:
# split into train and test
split = 0.1
total_size = len(y)
valid_size = int(split * total_size)
test_size = int(split * total_size)
trainX, testX = train_test_split(X, test_size=test_size, random_state=42)
trainy, testy = train_test_split(y, test_size=test_size, random_state=42)

In [12]:
# define model
model = Sequential()
model.add(Dense(16, input_dim=3, activation='relu', kernel_initializer='he_uniform'))
model.add(tf.keras.layers.Dense(24, activation='relu'))
model.add(tf.keras.layers.Dense(16, activation='relu'))
model.add(Dense(1, activation='linear'))

2023-03-12 13:57:51.391074: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [13]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense (Dense)               (None, 16)                64        
                                                                 
 dense_1 (Dense)             (None, 24)                408       
                                                                 
 dense_2 (Dense)             (None, 16)                400       
                                                                 
 dense_3 (Dense)             (None, 1)                 17        
                                                                 
Total params: 889
Trainable params: 889
Non-trainable params: 0
_________________________________________________________________


In [14]:
if Train == True:
    opt = SGD(learning_rate=0.01, momentum=0.9)
    model.compile(loss='mean_squared_error', optimizer=opt)
    # fit model
    history = model.fit(trainX, trainy, validation_data=(testX, testy), epochs=100, verbose=2)
    # evaluate the model
    train_mse = model.evaluate(trainX, trainy, verbose=0)
    test_mse = model.evaluate(testX, testy, verbose=0)
    print('Train: %.3f, Test: %.3f' % (train_mse, test_mse))
    model.save_weights('NN_weights')

In [15]:
if Train == True:
    # plot loss during training
    plt.title('Loss / Mean Squared Error')
    plt.plot(history.history['loss'], label='train')
    plt.plot(history.history['val_loss'], label='test')
    plt.legend()
    plt.show()

In [16]:
if Train == False:
    model.load_weights('NN_weights')

In [17]:
num_rows = len(X_real)
latlon_full = []
for i in range(num_rows):
    latlon_full.append((X_real[i,0], X_real[i,1]))
linear_y = cm.LinearColormap(["red", "yellow", "green"], vmin=np.quantile(y_real,0.05), vmax=np.quantile(y_real,0.95))

In [18]:
map_raw = folium.Map( location=[37.424783, -122.163693], zoom_start=16)
for i, coord in enumerate(latlon_full):
    folium.Circle(location=[coord[0], coord[1]], fill_color=linear_y(y_real[i]), radius=3,\
                  color=linear_y(y_real[i]), fill_opacity=0.5,).add_to(map_raw)
map_raw

In [19]:
Directory = '/Users/shirleychen/Documents/Winter2023/AA272/Project/Predict/'
pathlist = Path(Directory).rglob('*.csv')
X_pred = np.zeros((1,3))
y_pred = np.zeros((1,1))
for path in pathlist:
    print(path)
    X1, y1 = data_process(path)
    X_pred = np.concatenate((X_pred,X1))
    y_pred = np.concatenate((y_pred,y1))
X_pred = X_pred[1:,:]
y_pred = y_pred[1:,:]

if Time_dep == False:
    X_pred = X_pred[:,0:2]

/Users/shirleychen/Documents/Winter2023/AA272/Project/Predict/02_22_08_55_20-LatLongVel.csv
/Users/shirleychen/Documents/Winter2023/AA272/Project/Predict/02_27_09_02_55-LatLongVel.csv


In [20]:
single_time = True
time_choice = "00:00:00"

Xp = np.copy(X_pred)
if single_time == True:
    x = time.strptime(time_choice,'%H:%M:%S')
    time_sec = datetime.timedelta(hours=x.tm_hour,minutes=x.tm_min,seconds=x.tm_sec).total_seconds()
    print("Time in seconds:", time_sec)
    if Time_dep == True:
        Xp[:,2] = time_sec

scaler = load('scaler.joblib')
Xp_trans = scaler.transform(Xp)
yp = model.predict(Xp_trans)

Time in seconds: 0.0
26/26 [==============================] - 0s 999us/step


In [27]:
num_rows = len(X_pred)
latlon = []
for i in range(num_rows):
    latlon.append((X_pred[i,0], X_pred[i,1]))
linear_y = cm.LinearColormap(["red", "yellow", "green"], vmin=np.quantile(y,0.05), vmax=np.quantile(y,0.95))
linear_yp = cm.LinearColormap(["red", "yellow", "green"], vmin=np.quantile(yp,0.05), vmax=np.quantile(yp,0.95))

map_pred_scale = folium.Map( location=[37.424783, -122.163693], zoom_start=16)
for i, coord in enumerate(latlon):
    folium.Circle(location=[coord[0], coord[1]], fill_color=linear_yp(yp[i]), radius=3,\
                  color=linear_yp(yp[i]), fill_opacity=0.5,).add_to(map_pred_scale)
map_pred_scale

In [22]:
linear_yp

In [23]:
# for if standardizing
linear_y_scaled = cm.LinearColormap(["red", "yellow", "green"], vmin=np.quantile(y_real_scaled,0.05), vmax=np.quantile(y_real_scaled,0.95))
map_raw_scale = folium.Map( location=[37.424783, -122.163693], zoom_start=16)
for i, coord in enumerate(latlon):
    folium.Circle(location=[coord[0], coord[1]], fill_color=linear_y_scaled(yp[i]), radius=3,\
                  color=linear_y_scaled(yp[i]), fill_opacity=1.0,).add_to(map_raw_scale)
map_raw_scale

In [24]:
#predict time
dist_vec = []
for i in range(len(X_pred)-1):
    dist_vec.append(np.sqrt((abs(X_pred[i+1,0] - X_pred[i,0])*111194.9266)**2+(abs(X_pred[i+1,1] - X_pred[i,1])*88303.18818)**2))

In [25]:
scalery = load('scalery.joblib')
yp_rescaled = scalery.inverse_transform(yp)
i = 0
Directory = '/Users/shirleychen/Documents/Winter2023/AA272/Project/Predict/'
pathlist = Path(Directory).rglob('*.csv')
for path in pathlist:
    X1, y1 = data_process(path)
    print(path)
    time_est = 0
    for j in range(i,i+len(X1)-1):
        time_est += (dist_vec[j]/yp_rescaled[j])
    print("Est Transit Time:", str(datetime.timedelta(seconds=int(time_est[0]))))
    i += len(y1)
    print("True Transit Time", str(datetime.timedelta(seconds=(X1[-1,2]-X1[0,2]))))

/Users/shirleychen/Documents/Winter2023/AA272/Project/Predict/02_22_08_55_20-LatLongVel.csv
Est Transit Time: 0:02:43
True Transit Time 0:03:46
/Users/shirleychen/Documents/Winter2023/AA272/Project/Predict/02_27_09_02_55-LatLongVel.csv
Est Transit Time: 0:02:16
True Transit Time 0:02:51
